<a href="https://colab.research.google.com/github/amehregan25/Lead-Assistant/blob/main/marketing_app_colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# Colab / widget setup
%pip install ipywidgets --quiet

from google.colab import files
from IPython.display import display, Markdown, clear_output
import importlib
import textwrap

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 20.1 MB/s eta 0:00:00


In [3]:
# Upload Python script and CSVs for this session
print("Upload interactive_marketing.py and any required CSVs (e.g. install base, campaign history).")
uploaded = files.upload()

uploaded

Upload interactive_marketing.py and any required CSVs (e.g. install base, campaign history).


Saving report1765405239456.csv to report1765405239456 (1).csv
Saving interactive_marketing.py to interactive_marketing (1).py


{'report1765405239456 (1).csv': b'"Campaign ID","Campaign Name","Member Type","Member First Associated Date","First Name","Last Name","Related Record ID"\n"701Sq000009LlDF","NUR-2024-05 General Nurture v1","Contact","10/3/2025","Jennifer","Kay","0038d000002x4lx"\n"701Sq00000aQCgs","PROMO-25 End of Year Budget Push - Email Closed Lost","Contact","9/30/2025","Jennifer","Kay","0038d000002x4lx"\n"701Sq00000AyVrC","24-09-DOT-Reception","Contact","9/17/2024","Ammar","Arsiwala","0038d000002x6An"\n"7018d000000Lm4e","Contact Us Form (Generic)","Contact","9/12/2023","Kirsi","Mattinen","0038d000002xeew"\n"7018d000000Lnpf","Webinar - Protein Expression Re-imagined","Contact","6/28/2023","Kirsi","Mattinen","0038d000002xeew"\n"701Sq000009LlDF","NUR-2024-05 General Nurture v1","Contact","10/3/2025","Kirsi","Mattinen","0038d000002xeew"\n"701Sq00000YuZUN","Webinar 2025-11-04 Mastering membrane proteins","Contact","10/23/2025","Kirsi","Mattinen","0038d000002xeew"\n"701Sq00000aQCgs","PROMO-25 End of Year

In [4]:
import interactive_marketing
importlib.reload(interactive_marketing)  # so you can re-upload and re-run if needed

# Quick smoke test (optional)
print("Module loaded. Available attributes:")
print([name for name in dir(interactive_marketing) if "recommendation" in name.lower()])

Module loaded. Available attributes:
['generate_recommendation_report']


In [5]:
def render_report(report: dict):
    clear_output(wait=True)

    lines = []

    # Header
    lines.append(f"### Recommendation Summary")
    lines.append("")
    lines.append(f"- **Segment**: {report.get('segment', 'N/A')}")
    lines.append(f"- **Persona**: {report.get('persona', 'N/A')}")
    lines.append(f"- **Workflow**: {report.get('topic', 'generic')}")

    # Current customer / install base
    install_info = report.get("install_base_info")
    if install_info:
        lines.append("")
        lines.append("#### Current Customer")
        acc = install_info.get("account_name", "Unknown account")
        loc = install_info.get("location", "Unknown location")
        lines.append(f"- Existing **eProtein Discovery** system at **{acc}** ({loc})")
        if install_info.get("note"):
            lines.append(f"- Note: {install_info['note']}")

    # Case studies
    cases = report.get("recommended_cases", [])
    if cases:
        lines.append("")
        lines.append("#### Recommended Case Studies")
        for case in cases:
            name = case.get("name", "Untitled case")
            summary = case.get("summary", "").strip()
            lines.append(f"- **{name}**")
            if summary:
                wrapped = textwrap.fill(summary, width=90)
                lines.append(f"  - {wrapped}")
    else:
        lines.append("")
        lines.append("#### Recommended Case Studies")
        lines.append("- No direct case-study overlap; suggest sharing general workflow resources.")

    # Collateral suggestions
    resources = report.get("suggested_resources", [])
    if resources:
        lines.append("")
        lines.append("#### Suggested Collateral")
        for r in resources:
            lines.append(f"- {r}")

    # Campaign history
    history = report.get("campaign_history", [])
    if history:
        lines.append("")
        lines.append("#### Prior Campaign Membership")
        for item in history:
            cname = item.get("campaign_name", "Unknown campaign")
            date = item.get("first_associated_date", "N/A")
            lines.append(f"- {cname} (first associated: {date})")

    md = "\n".join(lines)
    display(Markdown(md))

In [6]:
import ipywidgets as widgets

# Input widgets
first_name_w = widgets.Text(
    description="First name",
    placeholder="e.g. Paul",
    layout=widgets.Layout(width="50%")
)

last_name_w = widgets.Text(
    description="Last name",
    placeholder="e.g. Agianian",
    layout=widgets.Layout(width="50%")
)

title_w = widgets.Text(
    description="Title",
    placeholder="e.g. Principal Scientist, Protein Engineering",
    layout=widgets.Layout(width="70%")
)

company_w = widgets.Text(
    description="Company",
    placeholder="e.g. Pfizer",
    layout=widgets.Layout(width="70%")
)

workflow_w = widgets.Dropdown(
    description="Workflow",
    options=[
        ("Auto / generic", ""),
        ("Soluble", "soluble"),
        ("Membrane", "membrane"),
        ("Antibody", "antibody"),
    ],
    value="",
    layout=widgets.Layout(width="50%")
)

protein_targets_w = widgets.Text(
    description="Protein(s)",
    placeholder="e.g. GIPR, GCGR, FFAR1",
    layout=widgets.Layout(width="90%")
)

therapeutic_areas_w = widgets.Text(
    description="Therapeutic areas",
    placeholder="e.g. oncology, metabolic disease, neurodegeneration",
    layout=widgets.Layout(width="90%")
)

linkedin_summary_w = widgets.Textarea(
    description="LinkedIn summary",
    placeholder="Paste the lead's LinkedIn summary here (optional)…",
    layout=widgets.Layout(width="90%", height="120px")
)

run_button = widgets.Button(
    description="Generate recommendations",
    button_style="primary",
    layout=widgets.Layout(width="50%")
)

output_area = widgets.Output()

def on_run_clicked(b):
    with output_area:
        output_area.clear_output()

        title = title_w.value.strip()
        company = company_w.value.strip()
        workflow = workflow_w.value or ""  # maps to topic_input
        protein_targets = protein_targets_w.value.strip()
        therapeutic_areas = therapeutic_areas_w.value.strip()
        linkedin_summary = linkedin_summary_w.value.strip()
        first_name = first_name_w.value.strip()
        last_name = last_name_w.value.strip()

        report = interactive_marketing.generate_recommendation_report(
            title=title,
            company=company,
            topic_input=workflow,      # if your function uses 'workflow=', change this name
            protein_targets=protein_targets,
            therapeutic_areas=therapeutic_areas,
            linkedin_summary=linkedin_summary,
            first_name=first_name,
            last_name=last_name,
        )

        render_report(report)

run_button.on_click(on_run_clicked)

# Layout
form_items = widgets.VBox([
    widgets.HTML("<h3>Lead & Context</h3>"),
    widgets.HBox([first_name_w, last_name_w]),
    title_w,
    company_w,
    workflow_w,
    protein_targets_w,
    therapeutic_areas_w,
    linkedin_summary_w,
    run_button,
])

app = widgets.VBox([form_items, output_area])
display(app)